##### Copyright 2021 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# 迁移评估

<table class="tfo-notebook-buttons" align="left">
  <td>     <a target="_blank" href="https://tensorflow.google.cn/guide/migrate/evaluator"><img src="https://tensorflow.google.cn/images/tf_logo_32px.png">在 TensorFlow.org 上查看</a>   </td>
  <td>     <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/migrate/evaluator.ipynb"><img src="https://tensorflow.google.cn/images/colab_logo_32px.png">在 Google Colab 运行</a>
</td>
  <td>     <a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/zh-cn/guide/migrate/evaluator.ipynb"><img src="https://tensorflow.google.cn/images/GitHub-Mark-32px.png">在 Github 上查看源代码</a>
</td>
  <td>     <a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/zh-cn/guide/migrate/evaluator.ipynb"><img src="https://tensorflow.google.cn/images/download_logo_32px.png">下载笔记本</a>   </td>
</table>

评估是对模型进行衡量和基准测试的关键部分。

本指南演示了如何将评估器任务从 TensorFlow 1 迁移到 TensorFlow 2。在 TensorFlow 1 中，当 API 以分布式方式运行时，此功能由 `tf.estimator.train_and_evaluate` 实现。在 Tensorflow 2 中，可以使用内置 `tf.keras.utils.SidecarEvaluator`，或在评估器任务上使用自定义评估循环。

TensorFlow 1 (`tf.estimator.Estimator.evaluate`) 和 TensorFlow 2（`Model.fit(..., validation_data=(...))` 或 `Model.evaluate`）中都有简单的连续评估选项。当您不希望工作进程在训练和评估之间切换时，评估器任务更合适，而当您希望分布评估时，`Model.fit` 中的内置评估更合适。


## 安装

In [2]:
import tensorflow.compat.v1 as tf1
import tensorflow as tf
import numpy as np
import tempfile
import time
import os

2022-12-14 20:55:51.655222: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 20:55:51.655311: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 20:55:51.655320: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


In [3]:
mnist = tf.keras.datasets.mnist

(x_train, y_train),(x_test, y_test) = mnist.load_data()
x_train, x_test = x_train / 255.0, x_test / 255.0

## TensorFlow 1：使用 tf.estimator.train_and_evaluate 进行评估

在 TensorFlow 1 中，可以配置 `tf.estimator` 以使用 `tf.estimator.train_and_evaluate` 评估 Estimator。

在此示例中，首先定义 `tf.estimator.Estimator` 并指定训练和评估规范：

In [4]:
feature_columns = [tf1.feature_column.numeric_column("x", shape=[28, 28])]

classifier = tf1.estimator.DNNClassifier(
    feature_columns=feature_columns,
    hidden_units=[256, 32],
    optimizer=tf1.train.AdamOptimizer(0.001),
    n_classes=10,
    dropout=0.2
)

train_input_fn = tf1.estimator.inputs.numpy_input_fn(
    x={"x": x_train},
    y=y_train.astype(np.int32),
    num_epochs=10,
    batch_size=50,
    shuffle=True,
)

test_input_fn = tf1.estimator.inputs.numpy_input_fn(
    x={"x": x_test},
    y=y_test.astype(np.int32),
    num_epochs=10,
    shuffle=False
)

train_spec = tf1.estimator.TrainSpec(input_fn=train_input_fn, max_steps=10)
eval_spec = tf1.estimator.EvalSpec(input_fn=test_input_fn,
                                   steps=10,
                                   throttle_secs=0)

INFO:tensorflow:Using default config.


INFO:tensorflow:Using config: {'_model_dir': '/tmpfs/tmp/tmprtyymqc8', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_session_creation_timeout_secs': 7200, '_checkpoint_save_graph_def': True, '_service': None, '_cluster_spec': ClusterSpec({}), '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


随后，训练和评估模型。评估在训练之间同步运行，因为它在此笔记本中被限制为本地运行，并且在训练和评估之间交替运行。但是，如果 Estimator 是以分布式方式使用的，则评估器将作为专用评估器任务运行。有关详情，请查看[分布式训练的迁移指南](https://tensorflow.google.cn/guide/migrate/multi_worker_cpu_gpu_training)。

In [5]:
tf1.estimator.train_and_evaluate(estimator=classifier,
                                train_spec=train_spec,
                                eval_spec=eval_spec)

INFO:tensorflow:Not using Distribute Coordinator.


INFO:tensorflow:Running training and evaluation locally (non-distributed).


INFO:tensorflow:Start train and evaluate loop. The evaluate will happen after every checkpoint. Checkpoint frequency is determined based on RunConfig arguments: save_checkpoints_steps None or save_checkpoints_secs 600.


Instructions for updating:
Use Variable.read_value. Variables in 2.X are initialized automatically both in eager and graph (inside tf.defun) contexts.


Instructions for updating:
To construct input pipelines, use the `tf.data` module.


...

INFO:tensorflow:Finished evaluation at 2022-12-14-20:55:59


INFO:tensorflow:Saving dict for global step 10: accuracy = 0.46953124, average_loss = 1.9085802, global_step = 10, loss = 244.29826


INFO:tensorflow:Saving 'checkpoint_path' summary for global step 10: /tmpfs/tmp/tmprtyymqc8/model.ckpt-10


INFO:tensorflow:Loss for final step: 89.78812.


({'accuracy': 0.46953124,
  'average_loss': 1.9085802,
  'loss': 244.29826,
  'global_step': 10},
 [])

## TensorFlow 2：评估 Keras 模型

在 TensorFlow 2 中，如果您使用 `Model.fit` API 进行训练，则可以使用 `tf.keras.utils.SidecarEvaluator` 评估模型。此外，还可以在 Tensorboard 中呈现评估指标，本指南中未介绍此功能。

为了帮助演示这一点，我们首先定义和训练模型：


In [6]:
def create_model():
  return tf.keras.models.Sequential([
    tf.keras.layers.Flatten(input_shape=(28, 28)),
    tf.keras.layers.Dense(512, activation='relu'),
    tf.keras.layers.Dropout(0.2),
    tf.keras.layers.Dense(10)
  ])

loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)

model = create_model()
model.compile(optimizer='adam',
              loss=loss,
              metrics=['accuracy'],
              steps_per_execution=10,
              run_eagerly=True)

log_dir = tempfile.mkdtemp()
model_checkpoint = tf.keras.callbacks.ModelCheckpoint(
    filepath=os.path.join(log_dir, 'ckpt-{epoch}'),
    save_weights_only=True)

model.fit(x=x_train,
          y=y_train,
          epochs=1,
          callbacks=[model_checkpoint])

  10/1875 [..............................] - ETA: 2:30 - loss: 1.8265 - accuracy: 0.4281

  20/1875 [..............................] - ETA: 1:30 - loss: 1.4352 - accuracy: 0.5703

  30/1875 [..............................] - ETA: 1:09 - loss: 1.2100 - accuracy: 0.6375

  40/1875 [..............................] - ETA: 59s - loss: 1.0624 - accuracy: 0.6836 

  50/1875 [..............................] - ETA: 53s - loss: 0.9504 - accuracy: 0.7175

...

1850/1875 [============================>.] - ETA: 0s - loss: 0.2226 - accuracy: 0.9341

1860/1875 [============================>.] - ETA: 0s - loss: 0.2220 - accuracy: 0.9343

1870/1875 [============================>.] - ETA: 0s - loss: 0.2216 - accuracy: 0.9344

1875/1875 [==============================] - ETA: 0s - loss: 0.2213 - accuracy: 0.9345

1875/1875 [==============================] - 32s 17ms/step - loss: 0.2213 - accuracy: 0.9345


然后，使用 `tf.keras.utils.SidecarEvaluator` 评估模型。在实际训练中，建议使用单独的作业进行评估，以释放工作进程资源进行训练。

In [7]:
data = tf.data.Dataset.from_tensor_slices((x_test, y_test))
data = data.batch(64)

tf.keras.utils.SidecarEvaluator(
    model=model,
    data=data,
    checkpoint_dir=log_dir,
    max_evaluations=1
).start()

INFO:tensorflow:Waiting for new checkpoint at /tmpfs/tmp/tmp37hqk452


INFO:tensorflow:Found new checkpoint at /tmpfs/tmp/tmp37hqk452/ckpt-1


INFO:tensorflow:Evaluation starts: Model weights loaded from latest checkpoint file /tmpfs/tmp/tmp37hqk452/ckpt-1


157/157 - 2s - loss: 0.1017 - accuracy: 0.9683 - 2s/epoch - 10ms/step


INFO:tensorflow:End of evaluation. Metrics: loss=0.10172463953495026 accuracy=0.9682999849319458


INFO:tensorflow:Last checkpoint evaluated. SidecarEvaluator stops.


## 后续步骤

- 要详细了解 sidecar 评估，请考虑阅读 `tf.keras.utils.SidecarEvaluator` API 文档。
- 要考虑在 Keras 中交替进行训练和评估，请考虑阅读[其他内置方法](https://tensorflow.google.cn/guide/keras/train_and_evaluate)。